In [99]:
import os

import matplotlib.pyplot as plt
import pyLDAvis

from gensim.corpora import Dictionary

import spacy
from math import nan
from itertools import chain
import gensim
from gensim.parsing.preprocessing import *
import pandas as pd

import nltk

nltk.download('omw-1.4')
nltk.download('wordnet')

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 50)
pd.set_option('display.width', 1000)

[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\danie\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\danie\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [85]:
try:
    df = pd.read_feather('data/df_concat.featherSSSSSSSSSSSSSSSSSSSSSSSSS')
except FileNotFoundError:
    df = pd.read_csv('data/train.csv')

print(
    df.isnull().sum()
)

df.replace(nan, 'unknown', inplace=True)

df.head()



id           0
title      558
author    1957
text        39
label        0
dtype: int64


id                                              title              author                                               text  label
0   0  House Dem Aide: We Didn’t Even See Comey’s Let...       Darrell Lucus  House Dem Aide: We Didn’t Even See Comey’s Let...      1
1   1  FLYNN: Hillary Clinton, Big Woman on Campus - ...     Daniel J. Flynn  Ever get the feeling your life circles the rou...      0
2   2                  Why the Truth Might Get You Fired  Consortiumnews.com  Why the Truth Might Get You Fired October 29, ...      1
3   3  15 Civilians Killed In Single US Airstrike Hav...     Jessica Purkiss  Videos 15 Civilians Killed In Single US Airstr...      1
4   4  Iranian woman jailed for fictional unpublished...      Howard Portnoy  Print \nAn Iranian woman has been sentenced to...      1

In [86]:
df = df.iloc[:, 1:]
df.head()

title              author                                               text  label
0  House Dem Aide: We Didn’t Even See Comey’s Let...       Darrell Lucus  House Dem Aide: We Didn’t Even See Comey’s Let...      1
1  FLYNN: Hillary Clinton, Big Woman on Campus - ...     Daniel J. Flynn  Ever get the feeling your life circles the rou...      0
2                  Why the Truth Might Get You Fired  Consortiumnews.com  Why the Truth Might Get You Fired October 29, ...      1
3  15 Civilians Killed In Single US Airstrike Hav...     Jessica Purkiss  Videos 15 Civilians Killed In Single US Airstr...      1
4  Iranian woman jailed for fictional unpublished...      Howard Portnoy  Print \nAn Iranian woman has been sentenced to...      1

In [87]:
df['title'].value_counts()

unknown                                                                                                         558
Get Ready For Civil Unrest: Survey Finds That Most Americans Are Concerned About Election Violence                5
The Dark Agenda Behind Globalism And Open Borders                                                                 5
Schools All Over America Are Closing On Election Day Due To Fears Of Violence                                     4
Las imágenes libres de derechos más destacadas de la semana                                                       4
                                                                                                               ... 
Report: Only 6% of Millennials Said Their Social Media Was a ’Completely True’ Depiction of Them - Breitbart      1
Hillary Clinton, Donald Trump, Iraq Inquiry: Your Wednesday Evening Briefing - The New York Times                 1
Shall We Save Civilization, or Not? - American Herald Tribune           

In [88]:
df['author_text'] = df['author'] + ' ' + df['title'] + ' ' + df['text']
df['author_text']

0        Darrell Lucus House Dem Aide: We Didn’t Even S...
1        Daniel J. Flynn FLYNN: Hillary Clinton, Big Wo...
2        Consortiumnews.com Why the Truth Might Get You...
3        Jessica Purkiss 15 Civilians Killed In Single ...
4        Howard Portnoy Iranian woman jailed for fictio...
                               ...                        
20795    Jerome Hudson Rapper T.I.: Trump a ’Poster Chi...
20796    Benjamin Hoffman N.F.L. Playoffs: Schedule, Ma...
20797    Michael J. de la Merced and Rachel Abrams Macy...
20798    Alex Ansary NATO, Russia To Hold Parallel Exer...
20799    David Swanson What Keeps the F-35 Alive   Davi...
Name: author_text, Length: 20800, dtype: object

In [91]:
def is_ascii(letter):
    letter = letter[0]

    if letter in string.ascii_letters:
        return True
    return False


df['lang'] = df['text'].apply(is_ascii)

df = df[df['lang'] == True]

print(len(df))
CUSTOM_FILTERS = [remove_stopwords, stem_text,
                  strip_non_alphanum, strip_multiple_whitespaces, strip_short]

tokens = [preprocess_string(doc, CUSTOM_FILTERS) for doc in df['author_text']]

18463


In [92]:
df['clean'] = tokens

df['clean_join'] = df['clean'].apply(lambda x: ' '.join(x))
df['length'] = df['clean'].apply(lambda x: len(x))

C:\Users\danie\AppData\Local\Temp/ipykernel_26604/3076016838.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['clean'] = tokens
C:\Users\danie\AppData\Local\Temp/ipykernel_26604/3076016838.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['clean_join'] = df['clean'].apply(lambda x: ' '.join(x))
C:\Users\danie\AppData\Local\Temp/ipykernel_26604/3076016838.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = valu

In [94]:
all_words = list(chain.from_iterable(df['clean']))
num_words = len(set(all_words))

print(
    f'all words: {len(all_words)}\n'
    f'unique words: {num_words}'
)

all words: 7696107
unique words: 145350


In [95]:
df.reset_index().to_feather('data/df_concat.feather')

In [96]:
mydict = Dictionary(tokens)
mydict.token2id

mycorpus = [mydict.doc2bow(doc, allow_update=True) for doc in tokens]

word_counts = [[(mydict[id], count) for id, count in line]
               for line in mycorpus]

In [97]:
flat_counts = [i for s in word_counts for i in s]
flat_counts

[('2012', 1),
 ('2016', 2),
 ('ablaz', 1),
 ('about', 1),
 ('abus', 1),
 ('accord', 3),
 ('act', 1),
 ('actual', 1),
 ('advanc', 1),
 ('after', 2),
 ('agenc', 1),
 ('aid', 1),
 ('aide', 5),
 ('all', 2),
 ('american', 1),
 ('anchor', 1),
 ('and', 2),
 ('announc', 1),
 ('answer', 1),
 ('anthoni', 1),
 ('apolog', 1),
 ('appar', 2),
 ('appear', 1),
 ('attempt', 1),
 ('avail', 1),
 ('basic', 1),
 ('bipartisanship', 1),
 ('boss', 1),
 ('briefli', 1),
 ('bui', 1),
 ('burton', 1),
 ('but', 4),
 ('can', 1),
 ('carolina', 1),
 ('case', 4),
 ('chaffetz', 15),
 ('chairman', 2),
 ('chairmen', 4),
 ('charismat', 1),
 ('check', 1),
 ('christian', 2),
 ('classifi', 1),
 ('click', 1),
 ('clinton', 1),
 ('colleagu', 1),
 ('colleg', 1),
 ('comei', 5),
 ('comey', 6),
 ('committe', 6),
 ('committee', 1),
 ('commons', 1),
 ('connect', 2),
 ('consid', 1),
 ('contain', 1),
 ('control', 1),
 ('cook', 1),
 ('cooler', 1),
 ('counterpart', 1),
 ('course', 1),
 ('courtesi', 2),
 ('creativ', 1),
 ('cum', 1),
 ('dai

In [98]:
import pickle

pickle.dump(mycorpus, open('mycorpus.pkl', 'wb'))
mydict.save('corp_dict.gensim')

In [100]:
#
# tf_idf = models.TfidfModel(mycorpus)
#
# trans_tf_idf = tf_idf[mycorpus]
# print(trans_tf_idf)

In [103]:
% % timeit

lda = models.LdaMulticore(
    corpus=mycorpus,
    id2word=mydict,
    workers=6
)



14.7 s ± 184 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [104]:
lda.show_topics()

[(0,
  '0.001*"trump" + 0.001*"clinton" + 0.001*"said" + 0.001*"polic" + 0.001*"obama" + 0.001*"hillari" + 0.001*"fbi" + 0.001*"campaign" + 0.000*"state" + 0.000*"offic"'),
 (1,
  '0.002*"trump" + 0.001*"clinton" + 0.001*"said" + 0.001*"obama" + 0.001*"vote" + 0.001*"democrat" + 0.001*"russia" + 0.001*"republican" + 0.001*"hillari" + 0.001*"elect"'),
 (2,
  '0.001*"trump" + 0.001*"clinton" + 0.001*"said" + 0.001*"russia" + 0.001*"vote" + 0.001*"republican" + 0.001*"obama" + 0.001*"state" + 0.001*"hillari" + 0.001*"elect"'),
 (3,
  '0.001*"trump" + 0.001*"clinton" + 0.001*"said" + 0.001*"russia" + 0.001*"vote" + 0.001*"russian" + 0.001*"obama" + 0.001*"state" + 0.001*"war" + 0.001*"hillari"'),
 (4,
  '0.002*"trump" + 0.001*"clinton" + 0.001*"said" + 0.001*"vote" + 0.001*"republican" + 0.001*"russia" + 0.001*"elect" + 0.001*"state" + 0.001*"democrat" + 0.001*"american"'),
 (5,
  '0.001*"trump" + 0.001*"clinton" + 0.001*"said" + 0.001*"russia" + 0.001*"state" + 0.001*"hillari" + 0.001*"ob

In [107]:
# import pyLDAvis.graphlab
import pyLDAvis.gensim_models as gensimvis

pyLDAvis.enable_notebook()

gensimvis.prepare(lda, mycorpus, mydict)
# pyLDAvis.prepare()
# vis = pyLDAvis.prepare(lda, mycorpus, mydict)

C:\Users\danie\anaconda3\envs\project-4\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  by='saliency', ascending=False).head(R).drop('saliency', 1)


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1      0.006395  0.001189       1        1  29.002271
2      0.007500  0.001458       2        1  21.163559
4      0.006663  0.000768       3        1  17.788411
7      0.000680  0.003864       4        1   8.251707
3     -0.000134 -0.012712       5        1   5.850355
9     -0.003121 -0.001259       6        1   5.404084
5     -0.000230 -0.006012       7        1   4.292625
6     -0.000967  0.004772       8        1   3.111264
0     -0.014355  0.000789       9        1   2.644731
8     -0.002429  0.007145      10        1   2.490994, topic_info=         Term          Freq         Total Category  logprob  loglift
494     trump  12490.000000  12490.000000  Default  30.0000  30.0000
43    clinton   8244.000000   8244.000000  Default  29.0000  29.0000
464      said   6003.000000   6003.000000  Default  28.0000  28.0000
111   hillari   4402.000000   4402.000000  Default  27.0000  27.0000
95        fbi   3241.000000   3241.000000  Default  26.0000  26.0000
..        ...           ...           ...      ...      ...      ...
293    attack     74.868647   2962.082816  Topic10  -7.8480   0.0146
351     elect     86.931024   4134.589286  Topic10  -7.6986  -0.1695
430       new     78.743430   3327.704395  Topic10  -7.7975  -0.0514
14   american     82.588290   3911.789341  Topic10  -7.7499  -0.1654
437     peopl     78.039495   3524.251390  Topic10  -7.8065  -0.1177

[819 rows x 6 columns], token_table=       Topic      Freq      Term
term                            
58894      1  0.196692     122bn
58894      2  0.163910     122bn
58894      3  0.131128     122bn
58894      4  0.065564     122bn
58894      5  0.032782     122bn
...      ...       ...       ...
57546      6  0.038852  ᵛᵉʳᶦᶠᶦᵉᵈ
57546      7  0.019426  ᵛᵉʳᶦᶠᶦᵉᵈ
57546      8  0.038852  ᵛᵉʳᶦᶠᶦᵉᵈ
57546      9  0.038852  ᵛᵉʳᶦᶠᶦᵉᵈ
57546     10  0.019426  ᵛᵉʳᶦᶠᶦᵉᵈ

[5190 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 3, 5, 8, 4, 10, 6, 7, 1, 9])

In [111]:
from gensim import models, similarities
import numpy as np

# tf_idf = models.TfidfModel(mycorpus)
lda_model = models.LdaMulticore(
    corpus=mycorpus,
    id2word=mydict,
    random_state=100,
    num_topics=7,
    passes=10,
    chunksize=1000,
    batch=False,
    alpha='asymmetric',
    decay=0.5,
    offset=64,
    eta=None,
    eval_every=0,
    iterations=100,
    gamma_threshold=0.001,
    per_word_topics=True)

# save the model
lda_model.save('lda_model.model')
# for item in tf_idf[mycorpus]:
#         print([[mydict[id], np.around(freq, decimals=2)] for id, freq in item])
gensimvis.prepare(lda_model, mycorpus, mydict)

C:\Users\danie\anaconda3\envs\project-4\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  by='saliency', ascending=False).head(R).drop('saliency', 1)


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
4     -0.132644  0.007163       1        1  56.510136
2     -0.122822  0.060485       2        1  20.269684
6     -0.108771 -0.002740       3        1  18.835067
1      0.021048 -0.039961       4        1   1.273998
3      0.010259  0.020524       5        1   1.268750
0      0.066275 -0.103987       6        1   1.036502
5      0.266655  0.058515       7        1   0.805863, topic_info=           Term           Freq          Total Category  logprob  loglift
237         the  103153.000000  103153.000000  Default  30.0000  30.0000
464        said   74348.000000   74348.000000  Default  29.0000  29.0000
494       trump   51313.000000   51313.000000  Default  28.0000  28.0000
430         new   44800.000000   44800.000000  Default  27.0000  27.0000
43      clinton   24810.000000   24810.000000  Default  26.0000  26.0000
...         ...            ...            ...      ...      ...      ...
447   president      77.116731    5208.901688   Topic7  -6.6899   0.6082
6104        www      69.658325     864.592100   Topic7  -6.7916   2.3024
237         the      78.597390  103153.842640   Topic7  -6.6709  -2.3586
4570        era      68.033459    1048.687696   Topic7  -6.8152   2.0857
5172       http      65.722880     964.082976   Topic7  -6.8498   2.1353

[622 rows x 6 columns], token_table=      Topic      Freq  Term
term                       
1         1  0.367231  2016
1         2  0.431761  2016
1         3  0.159130  2016
1         4  0.008249  2016
1         5  0.006578  2016
...     ...       ...   ...
4060      2  0.007170  zika
4060      3  0.022706  zika
4060      4  0.005975  zika
4060      5  0.001195  zika
4060      6  0.001195  zika

[2587 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[5, 3, 7, 2, 4, 1, 6])

In [110]:
tokens

[['darrel',
  'lucu',
  'hous',
  'dem',
  'aide',
  'didn',
  'even',
  'see',
  'comey',
  'letter',
  'until',
  'jason',
  'chaffetz',
  'tweet',
  'hous',
  'dem',
  'aide',
  'didn',
  'even',
  'see',
  'comey',
  'letter',
  'until',
  'jason',
  'chaffetz',
  'tweet',
  'darrel',
  'lucu',
  'octob',
  '2016',
  'subscrib',
  'jason',
  'chaffetz',
  'stump',
  'american',
  'fork',
  'utah',
  'imag',
  'courtesi',
  'michael',
  'jolley',
  'avail',
  'creativ',
  'commons',
  'license',
  'with',
  'apolog',
  'keith',
  'olbermann',
  'doubt',
  'worst',
  'person',
  'the',
  'world',
  'week',
  'fbi',
  'director',
  'jame',
  'comey',
  'but',
  'accord',
  'hous',
  'democrat',
  'aide',
  'look',
  'like',
  'know',
  'second',
  'worst',
  'person',
  'well',
  'turn',
  'comei',
  'sent',
  'now',
  'infam',
  'letter',
  'announc',
  'fbi',
  'look',
  'email',
  'relat',
  'hillari',
  'clinton',
  'email',
  'server',
  'rank',
  'democrat',
  'relev',
  'commit

In [113]:
import tensorflow as tf
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.model_selection import train_test_split as tts

import nltk
import re
from nltk.stem import PorterStemmer, WordNetLemmatizer
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize, sent_tokenize
import gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
import keras
from keras.preprocessing.text import one_hot, Tokenizer

from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Dense, Flatten, Embedding, Input, LSTM, Conv1D, MaxPool1D, Bidirectional
from keras.models import Model

x_train, x_test, y_train, y_test = tts(df['clean_join'], df['label'], test_size=0.2)

tokenizer = Tokenizer(num_words=num_words)
tokenizer.fit_on_texts(x_train)
trainings = tokenizer.texts_to_sequences(x_train)
testings = tokenizer.texts_to_sequences(x_test)

padded_train = pad_sequences(trainings, maxlen=40, padding='post', truncating='post')
padded_test = pad_sequences(testings, maxlen=40, truncating='post')


In [137]:
model = Sequential()
model.add(Embedding(num_words, output_dim=128))
model.add(Bidirectional(LSTM(128)))

model.add(Dense(128, activation='relu'))
model.add(Dense(1, activation='sigmoid'))
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
model.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_1 (Embedding)     (None, None, 128)         18604800  
                                                                 
 bidirectional_1 (Bidirectio  (None, 256)              263168    
 nal)                                                            
                                                                 
 dense_2 (Dense)             (None, 128)               32896     
                                                                 
 dense_3 (Dense)             (None, 1)                 129       
                                                                 
Total params: 18,900,993
Trainable params: 18,900,993
Non-trainable params: 0
_________________________________________________________________


In [138]:
y_train = np.asarray(y_train)

model.fit(
    padded_train,
    y_train,
    batch_size=64,
    validation_split=0.1,
    epochs=2,
    validation_data=(x_test, y_test),
    use_multiprocessing=True
)

Epoch 1/2
208/208 [==============================] - 31s 131ms/step - loss: 0.1299 - accuracy: 0.9456 - val_loss: 0.0537 - val_accuracy: 0.9858
Epoch 2/2
208/208 [==============================] - 28s 132ms/step - loss: 0.0154 - accuracy: 0.9962 - val_loss: 0.0438 - val_accuracy: 0.9858


In [136]:
model.save('fakenews_model.model')

INFO:tensorflow:Assets written to: fakenews_model.model\assets


INFO:tensorflow:Assets written to: fakenews_model.model\assets


In [120]:
make_pred = model.predict(padded_test)

preds = []

preds = [1 if make_pred[i].item() > 0.5 else 0 for i in range(len(make_pred))]

print(preds)

[0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 0, 1, 1, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 1, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 0, 1, 1, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 0, 1, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 1, 0, 1, 1, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 

In [123]:
from sklearn.metrics import accuracy_score

accuracy = accuracy_score(list(y_test), preds)

print("Model Accuracy : ", accuracy)

Model Accuracy :  0.9783373950717574
